# Message-Passing Graph Variational Autoencoder

Here I will use principles from message-passing graph neural networks to try to generate
molecules in a graph variational autoencoder. This is based on my solutions to 
`geometric-gnn-dojo/geometric_gnn_101.ipynb`
Some of the code has also been taken from there

might also want to consider autoregressive model

In [1]:
import importlib
import logging
import time
from mygenai.models.graphvae import PropertyConditionedVAE
# importlib.reload(PropertyConditionedVAE)

import torch
torch.cuda.empty_cache()
import torch_geometric
import numpy as np

import matplotlib.pyplot as plt
import seaborn as sns
import pandas as pd

print("PyTorch version {}".format(torch.__version__))
print("PyG version {}".format(torch_geometric.__version__))

PyTorch version 2.5.0+cu124
PyG version 2.6.1


In [2]:

debug_print = False
if debug_print:
    print("Debug mode is ON")
    logging.basicConfig(
        level=logging.DEBUG,
        format='%(asctime)s - %(name)s - %(levelname)s - %(message)s',
        force=True  # Ensure configuration is applied
    )
    for logger_name in ['train_epoch', 'PropertyConditionedVAE', 'ConditionalDecoder', 'Encoder']:
        logging.getLogger(logger_name).setLevel(logging.DEBUG)
else:
    print("Debug mode is OFF")
    logging.basicConfig(
        level=logging.INFO,
        format='%(asctime)s - %(name)s - %(levelname)s - %(message)s',
        force=True  # Ensure configuration is applied
    )
    for logger_name in ['train_epoch', 'PropertyConditionedVAE', 'ConditionalDecoder', 'Encoder']:
        logging.getLogger(logger_name).setLevel(logging.INFO)

Debug mode is OFF


In [3]:
import torch
from torch_geometric.datasets import QM9
from torch_geometric.loader import DataLoader
from sklearn.model_selection import train_test_split
import numpy as np
from mygenai.utils.transforms import CompleteGraph
from mygenai.utils.transforms import AddEdgeExistence

dataset = QM9(root="../data/QM9", transform=AddEdgeExistence()) #, transform=CompleteGraph())
# Normalize targets per data sample to mean = 0 and std = 1.
mean = dataset.data.y.mean(dim=0, keepdim=True)
std = dataset.data.y.std(dim=0, keepdim=True)
dataset.data.y = (dataset.data.y - mean) / std
# focus on just using the one-hot encoding of the atomic number, for simplicity for now
dataset.data.x = dataset.data.x[:, :5]

# Normalize distances in the dataset
fixed_max_distance = 2.0

# TODO in the future maybe use a Z matrix representation for positions
# def normalize_distances(dataset, max_distance):
#     for data in dataset:
#         pos = data.pos  # (n, 3) - absolute coordinates
#         src, dst = data.edge_index  # (2, num_edges) - edge indices
#         relative_positions = pos[dst] - pos[src]  # (num_edges, 3)
#         distances = torch.norm(relative_positions, dim=1)  # (num_edges,)
#         data.normalized_distances = distances / max_distance  # Normalize distances
#     return dataset

# dataset = normalize_distances(dataset, fixed_max_distance)
# min_atomic_number = 1
# max_atomic_number = 9
# dataset.data.z = (dataset.data.z - min_atomic_number) / (max_atomic_number - min_atomic_number) # doesn't actually matter because it's not used (this information is determined by data.x)

/home/jph/dev/generative-molecular-design/.conda/lib/python3.12/site-packages/torch_geometric/data/in_memory_dataset.py:300: UserWarning: It is not recommended to directly access the internal storage format `data` of an 'InMemoryDataset'. If you are absolutely certain what you are doing, access the internal storage via `InMemoryDataset._data` instead to suppress this warning. Alternatively, you can access stacked individual attributes of every graph via `dataset.{attr_name}`.
  warnings.warn(msg)


In [4]:
# Data splitting (60/20/20)
train_val_idx, test_idx = train_test_split(
    np.arange(len(dataset)),
    test_size=0.2,
    random_state=42
)
train_idx, val_idx = train_test_split(
    train_val_idx,
    test_size=0.25,
    random_state=42
)

train_loader = DataLoader(dataset[train_idx], batch_size=128, shuffle=True)
val_loader = DataLoader(dataset[val_idx], batch_size=128, shuffle=False)
test_loader = DataLoader(dataset[test_idx], batch_size=128, shuffle=False)

In [5]:
# Training setup
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
model = PropertyConditionedVAE().to(device)
optimizer = torch.optim.Adam(model.parameters(), lr=1e-3)
scheduler = torch.optim.lr_scheduler.ReduceLROnPlateau(
    optimizer, mode='min', factor=0.5, patience=5, min_lr=1e-6
)

In [6]:
# test forward passs
batch = next(iter(train_loader))
batch = batch.to(device)
with torch.no_grad():
    outputs = model(batch)
print("Forward pass successful!")

Forward pass successful!


In [7]:
# # check if training sets are reasonably balanced

# def basic_homo_lumo_stats(loader, name):
#     total_nodes = 0
#     total_graphs = 0
#     prop_values = []

#     for batch in loader:
#         total_graphs += batch.batch.max().item() + 1
#         total_nodes += batch.x.shape[0]
#         prop_values.append(batch.y[:, 4].cpu().numpy())

#     prop_values = np.concatenate(prop_values)
#     print(f"{name} stats - graphs: {total_graphs}, avg. nodes: {total_nodes/total_graphs}")
#     print(f"{name} property stats - mean: {prop_values.mean():.4f}, std: {prop_values.std():.4f}")

# basic_homo_lumo_stats(train_loader, "Train")
# basic_homo_lumo_stats(test_loader, "Test")
# basic_homo_lumo_stats(val_loader, "Validation")

In [8]:


# TODO : move training etc. to mygenai
# logging.basicConfig(level=logging.DEBUG)

# for now, check to see if can at least reconstruct molecules
recon_weight = 10.0
# kl_weight = 0.01
property_weight = 0.

def train_epoch(model, optimizer, train_loader, device, kl_weight):
    logger = logging.getLogger('train_epoch')
    model.train()
    total_loss = 0

    for batch_idx, batch in enumerate(train_loader):
        batch = batch.to(device)
        logger.debug(f"\nBatch {batch_idx}:")
        logger.debug(f"Batch properties: x={batch.x.shape}, pos={batch.pos.shape}, batch={batch.batch.shape}")
        optimizer.zero_grad()

        # Forward pass
        node_features, distances, directions, edge_features, num_nodes, edge_existence, mu, log_var, property_pred = model(batch)

        if batch_idx == 0:  # Check first batch only
            # Print statistics about generated values
            print(f"Generated node features: min={node_features.min().item():.4f}, max={node_features.max().item():.4f}")
            # print(f"Original node features: min={batch.x.min().item():.4f}, max={batch.x.max().item():.4f}") # always in [0,1] because one-hot encoding
            print(f"Generated distances: min={distances.min().item():.4f}, max={distances.max().item():.4f}")
            # print(f"Generated directions: min={directions.min().item():.4f}, max={directions.max().item():.4f}")

        # Calculate loss
        loss = model.loss_function(
            node_features, distances, directions, edge_features, num_nodes,
            edge_existence, batch, mu, log_var, property_pred,
            recon_weight=recon_weight, kl_weight=kl_weight, property_weight=property_weight
        )

        # Backward pass
        loss.backward()
        torch.nn.utils.clip_grad_norm_(model.parameters(), max_norm=1.)
        optimizer.step()

        total_loss += loss.item()

    return total_loss / len(train_loader)


def validate(model, val_loader, device, kl_weight):
    model.eval()
    total_loss = 0
    batch_losses = []

    with torch.no_grad():
        for batch_idx, batch in enumerate(val_loader):
            batch = batch.to(device)

            # Forward pass
            node_features, distances, directions, edge_features, num_nodes, edge_existence, mu, log_var, property_pred = model(batch)

            # Calculate loss
            loss = model.loss_function(
                node_features, distances, directions, edge_features, num_nodes,
                edge_existence, batch, mu, log_var, property_pred,
                recon_weight=recon_weight, kl_weight=kl_weight, property_weight=property_weight
            )

            batch_losses.append(loss.item())
            total_loss += loss.item()

    return total_loss / len(val_loader)


# Training loop
n_epochs = 100
best_val_loss = float('inf')
patience = 10
patience_counter = 0
initial_kl_weight = 0.00001
max_kl_weight = 0.001

# TODO ? use spherical coordinates again
batch = next(iter(train_loader))
logging.info(f"Target property shape: {batch.y.shape}")
logging.info(f"Target property sample: {batch.y[0]}")
logging.info(f"Input node features shape: {batch.x.shape}")  # Should be (N, 11)
logging.info(f"Input positions shape: {batch.pos.shape}")    # Should be (N, 3)
logging.info(f"Number of nodes: {batch.num_nodes}")
logging.info(f"Batch size: {batch.batch.max().item() + 1}")
for epoch in range(n_epochs):
    # KL annealing
    kl_weight = min(initial_kl_weight + 0.0001 * epoch, max_kl_weight)
    # Train
    train_loss = train_epoch(model, optimizer, train_loader, device, kl_weight)

    # Validate
    val_loss = validate(model, val_loader, device, kl_weight)

    # Learning rate scheduling
    scheduler.step(val_loss)

    # Early stopping
    if val_loss < best_val_loss:
        best_val_loss = val_loss
        patience_counter = 0
    else:
        patience_counter += 1
        if patience_counter >= patience:
            print(f'Early stopping at epoch {epoch}')
            # Save best model
            # Save model with timestamp in a more readable format
            timestamp = time.strftime("%Y%m%d_%H%M%S")
            save_path = f'best_vae_model_{timestamp}.pt'
            torch.save(model.state_dict(), save_path)
            print(f'Saved best model to: {save_path}')
            break

    # Print progress
    print(f'Epoch {epoch:03d} | Train Loss: {train_loss:.4f} | Val Loss: {val_loss:.4f}')

# Load best model for testing
# model.load_state_dict(torch.load('best_vae_model.pt'))

# Test final model
test_loss = validate(model, test_loader, device, kl_weight)
print(f'Final Test Loss: {test_loss:.4f}')

2025-04-21 22:50:03,098 - root - INFO - Target property shape: torch.Size([128, 19])
2025-04-21 22:50:03,099 - root - INFO - Target property sample: tensor([-0.2158,  1.2991,  0.5650, -0.8225, -1.0774, -0.0266,  0.3081,  0.6238,
         0.6238,  0.6238,  0.6238,  0.2047, -0.7757, -0.7725, -0.7694, -0.8127,
        -0.0043,  0.1716, -0.0911])
2025-04-21 22:50:03,099 - root - INFO - Input node features shape: torch.Size([2307, 5])
2025-04-21 22:50:03,099 - root - INFO - Input positions shape: torch.Size([2307, 3])
2025-04-21 22:50:03,100 - root - INFO - Number of nodes: 2307
2025-04-21 22:50:03,100 - root - INFO - Batch size: 128
2025-04-21 22:50:03,162 - PropertyConditionedVAE - INFO - Loss components - Node: 1.625857, Edge: 1.364066, Edge Existence: 0.663882, Distance: 0.048779, Direction: 0.987769, Num Nodes: 332.466614, KL: 0.140555, Property: 1.294601


Generated node features: min=0.0177, max=0.5999
Generated distances: min=0.4837, max=0.5977


2025-04-21 22:50:03,271 - PropertyConditionedVAE - INFO - Loss components - Node: 1.621696, Edge: 1.348304, Edge Existence: 0.639821, Distance: 0.043148, Direction: 1.006346, Num Nodes: 322.149475, KL: 0.146511, Property: 0.855097
2025-04-21 22:50:03,304 - PropertyConditionedVAE - INFO - Loss components - Node: 1.617667, Edge: 1.333063, Edge Existence: 0.603980, Distance: 0.040269, Direction: 1.012976, Num Nodes: 324.053223, KL: 0.156988, Property: 1.250725
2025-04-21 22:50:03,337 - PropertyConditionedVAE - INFO - Loss components - Node: 1.612107, Edge: 1.317469, Edge Existence: 0.577186, Distance: 0.035730, Direction: 1.004799, Num Nodes: 299.158630, KL: 0.160078, Property: 1.097972
2025-04-21 22:50:03,370 - PropertyConditionedVAE - INFO - Loss components - Node: 1.608618, Edge: 1.297523, Edge Existence: 0.547638, Distance: 0.033918, Direction: 1.012309, Num Nodes: 317.555847, KL: 0.157330, Property: 1.008453
2025-04-21 22:50:03,403 - PropertyConditionedVAE - INFO - Loss components - 

Epoch 000 | Train Loss: 10101.0291 | Val Loss: 2949.8330
Generated node features: min=0.0000, max=0.9984
Generated distances: min=0.2587, max=0.4239


2025-04-21 22:50:28,690 - PropertyConditionedVAE - INFO - Loss components - Node: 1.379511, Edge: 0.811824, Edge Existence: 0.000035, Distance: 0.027433, Direction: 1.004082, Num Nodes: 8.968157, KL: 4.959107, Property: 1.044082
2025-04-21 22:50:28,718 - PropertyConditionedVAE - INFO - Loss components - Node: 1.389247, Edge: 0.816527, Edge Existence: 0.000001, Distance: 0.029077, Direction: 1.002402, Num Nodes: 68.541626, KL: 4.929687, Property: 1.162964
2025-04-21 22:50:28,744 - PropertyConditionedVAE - INFO - Loss components - Node: 1.379190, Edge: 0.811367, Edge Existence: 0.000006, Distance: 0.028775, Direction: 1.013007, Num Nodes: 31.339161, KL: 4.986412, Property: 1.193821
2025-04-21 22:50:28,769 - PropertyConditionedVAE - INFO - Loss components - Node: 1.386329, Edge: 0.807419, Edge Existence: 0.000002, Distance: 0.029574, Direction: 1.009014, Num Nodes: 49.866947, KL: 4.974448, Property: 1.302740
2025-04-21 22:50:28,794 - PropertyConditionedVAE - INFO - Loss components - Node:

...

Epoch 027 | Train Loss: 1668.1037 | Val Loss: 1692.2352
Generated node features: min=0.0000, max=1.0000
Generated distances: min=0.3518, max=0.4614


2025-04-21 22:59:01,709 - PropertyConditionedVAE - INFO - Loss components - Node: 1.377271, Edge: 0.810278, Edge Existence: 0.000000, Distance: 0.027787, Direction: 1.004462, Num Nodes: 0.283106, KL: 8.120646, Property: 1.143312
2025-04-21 22:59:01,741 - PropertyConditionedVAE - INFO - Loss components - Node: 1.370168, Edge: 0.811794, Edge Existence: 0.000000, Distance: 0.027248, Direction: 1.004815, Num Nodes: 0.449397, KL: 8.072745, Property: 1.131270
2025-04-21 22:59:01,773 - PropertyConditionedVAE - INFO - Loss components - Node: 1.369287, Edge: 0.808749, Edge Existence: 0.000000, Distance: 0.027704, Direction: 1.005584, Num Nodes: 0.456238, KL: 8.076197, Property: 1.190173
2025-04-21 22:59:01,804 - PropertyConditionedVAE - INFO - Loss components - Node: 1.382100, Edge: 0.811550, Edge Existence: 0.000000, Distance: 0.027117, Direction: 1.007243, Num Nodes: 0.370245, KL: 8.091894, Property: 1.106305
2025-04-21 22:59:01,833 - PropertyConditionedVAE - INFO - Loss components - Node: 1.

Early stopping at epoch 28
Saved best model to: best_vae_model_20250421_225922.pt


2025-04-21 22:59:22,998 - PropertyConditionedVAE - INFO - Loss components - Node: 1.369283, Edge: 0.802637, Edge Existence: 0.000000, Distance: 0.027811, Direction: 1.001873, Num Nodes: 0.484125, KL: 8.069565, Property: 1.328793
2025-04-21 22:59:23,023 - PropertyConditionedVAE - INFO - Loss components - Node: 1.373182, Edge: 0.808359, Edge Existence: 0.000000, Distance: 0.027390, Direction: 0.997348, Num Nodes: 0.457782, KL: 8.073845, Property: 1.167492
2025-04-21 22:59:23,050 - PropertyConditionedVAE - INFO - Loss components - Node: 1.380435, Edge: 0.810052, Edge Existence: 0.000000, Distance: 0.027259, Direction: 0.997320, Num Nodes: 0.525035, KL: 8.084659, Property: 1.261602
2025-04-21 22:59:23,075 - PropertyConditionedVAE - INFO - Loss components - Node: 1.379207, Edge: 0.807926, Edge Existence: 0.000000, Distance: 0.027246, Direction: 1.001100, Num Nodes: 0.473536, KL: 8.065779, Property: 1.150386
2025-04-21 22:59:23,101 - PropertyConditionedVAE - INFO - Loss components - Node: 1.

Final Test Loss: 1673.3302


In [9]:
test_molecule = dataset[0]
test_molecule = test_molecule.to(device)

from torch_geometric.data import Batch
# Create a batch with a single molecule
test_batch = Batch.from_data_list([test_molecule])
outputs = model(test_batch)
node_features, distances, directions, edge_features, num_nodes, edge_existence, mu, log_var, property_pred = outputs

In [ ]:
# Print the generated node features
print("Generated node features:")
print(node_features)
print("Generated distances:")
print(distances)
print("Generated directions:")
print(directions)
print("Generated edge features:")
print(edge_features)
print("Generated num_nodes:")
print(num_nodes)
print("Generated edge_existence")
print(edge_existence)
print("Generated mu:")
print(mu)
print("Generated log_var:")
print(log_var)
print("Generated property prediction:")
print(property_pred)

Generated node features:
tensor([[1.0000e+00, 3.0248e-06, 5.5061e-09, 7.7771e-09, 1.1792e-08],
        [1.0000e+00, 3.0248e-06, 5.5061e-09, 7.7771e-09, 1.1792e-08],
        [1.0000e+00, 3.0248e-06, 5.5061e-09, 7.7771e-09, 1.1792e-08],
        [1.0000e+00, 3.0248e-06, 5.5061e-09, 7.7771e-09, 1.1792e-08],
        [1.0000e+00, 3.0248e-06, 5.5061e-09, 7.7771e-09, 1.1792e-08]],
       device='cuda:0', grad_fn=<SoftmaxBackward0>)
Generated distances:
tensor([[0.2442],
        [0.2442],
        [0.2442],
        [0.2442],
        [0.2442],
        [0.2442],
        [0.2442],
        [0.2442]], device='cuda:0', grad_fn=<SigmoidBackward0>)
Generated directions:
tensor([[ 0.9352,  0.1374,  0.3264],
        [ 0.7979,  0.3961,  0.4545],
        [ 0.1121,  0.9883,  0.1030],
        [ 0.9837, -0.0318,  0.1770],
        [-0.9352, -0.1374, -0.3264],
        [-0.7979, -0.3961, -0.4545],
        [-0.1121, -0.9883, -0.1030],
        [-0.9837,  0.0318, -0.1770]], device='cuda:0', grad_fn=<DivBackward0>)
G

In [11]:
from mygenai.utils.visualisation import visualise_molecule
visualise_molecule(test_molecule)

3Dmol.js failed to load for some reason. Please check your browser console for error messages.

In [12]:
# import importlib
# import mygenai.models.graphvae
# from mygenai.models.graphvae import PropertyConditionedVAE
# importlib.reload(mygenai.models.graphvae)
logging.getLogger('PropertyConditionedVAE').setLevel(logging.DEBUG)
batch_data = dataset[:100]
batch = Batch.from_data_list(batch_data).to(device)
with torch.no_grad():  # Disable gradient computation
    outputs = model(batch)
node_features, distances, directions, edge_features, num_nodes, mu, log_var, property_pred = outputs

# Compute the loss
loss = model.loss_function(
    node_features=node_features,
    distances=distances,
    directions=directions,
    edge_features=edge_features,
    num_nodes=num_nodes,
    data=batch,
    mu=mu,
    log_var=log_var,
    property_pred=property_pred,
    property_weight=property_weight,  # Use the same weights as during training
    recon_weight=recon_weight,
    kl_weight=kl_weight
)

2025-04-21 22:59:28,538 - PropertyConditionedVAE - DEBUG - Input data - batch_size: 100, nodes: 1005
2025-04-21 22:59:28,539 - PropertyConditionedVAE - DEBUG - Forward called without target_property (None)
2025-04-21 22:59:28,542 - PropertyConditionedVAE - DEBUG - Encoder outputs - mu: torch.Size([100, 32]), log_var: torch.Size([100, 32]), property_pred: torch.Size([100, 1])
2025-04-21 22:59:28,543 - PropertyConditionedVAE - DEBUG - Sampled z shape: torch.Size([100, 32])
2025-04-21 22:59:28,543 - PropertyConditionedVAE - DEBUG - Using encoder prediction for property, shape: torch.Size([100, 1])
2025-04-21 22:59:28,551 - PropertyConditionedVAE - DEBUG - Decoder outputs - node_features: torch.Size([1005, 5]), distances: torch.Size([1870, 1]), directions: torch.Size([1870, 3]), edge_features: torch.Size([1870, 4]), num_nodes: tensor([ 8.2952,  4.1956,  6.8610,  0.0251,  3.6303,  4.7032, 22.1258, 17.4323,
         9.1328,  7.2364, 10.4786, 11.0770, 22.6926, 17.6283, 18.5959, 12.7797,
     

ValueError: too many values to unpack (expected 8)